In [1]:
import ee
# ee.Authenticate()
ee.Initialize()

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from IPython.display import JSON
import altair as alt

In [4]:
col = ee.ImageCollection('MODIS/MYD09GA_006_NDVI').select('NDVI')

In [7]:
def get_relative_day(img):
    doy = img.date().getRelative('day', 'year')
    return img.set('doy', doy)
    
col = col.map(get_relative_day)

In [8]:
distinctDOY = col.filterDate('2013-01-01', '2014-01-01')

In [49]:
JSON(col.first().getInfo())

<IPython.core.display.JSON object>

In [ ]:
# filterdayofyear = ee.Filter.dayOfYear(48,49)
# tt = col.filter(filterdayofyear)

In [58]:
# JSON(tt.getInfo())

<IPython.core.display.JSON object>

In [9]:
filter_doy = ee.Filter.equals(leftField = 'doy', rightField = 'doy')
join = ee.Join.saveAll('doy_matches')

In [10]:
joinCol = ee.ImageCollection(join.apply(distinctDOY, col, filter_doy))

In [76]:
JSON(joinCol.getInfo())

<IPython.core.display.JSON object>

In [32]:
def get_mean(img):
    doyCol = ee.ImageCollection.fromImages(img.get('doy_matches'))
    doyCol_reduced = doyCol.reduce(ee.Reducer.median())
    return doyCol_reduced.set({'doy' : img.get('doy')})
    

In [33]:
mean_col = joinCol.map(get_mean)

In [35]:
# img0 = mean_col.first()
# img0.get('doy').getInfo()

0

In [34]:
JSON(mean_col.getInfo())

<IPython.core.display.JSON object>

In [16]:
# Define a function to transfer feature properties to a dictionary.
def fc_to_dict(fc):
    prop_names = fc.first().propertyNames()
    prop_lists = fc.reduceColumns(reducer=ee.Reducer.toList().repeat(prop_names.size()),
                                  selectors=prop_names).get('list') 
    return ee.Dictionary.fromLists(prop_names, prop_lists)

In [52]:
# a function for reducing gdd over a geometry 
def create_reduce_func_ndvi(geometry, reducer = ee.Reducer.mean(),band = 'NDVI_median'):
    def ndvi_on_img(img):
        ndvi = img.select(band)

        reduced_ndvi = ndvi.reduceRegion(reducer = reducer, geometry = geometry,scale = 1000)
        return ee.Feature(None, reduced_ndvi).set({'doy' : img.get('doy')})
    return ndvi_on_img

In [53]:
SD_counties = ee.FeatureCollection('TIGER/2018/Counties').filter(ee.Filter.eq('STATEFP', '46'))
SD_state = SD_counties.union().geometry()
f = create_reduce_func_ndvi(SD_state)
mean_reduced_ndvi = mean_col.map(f)

In [54]:
res = fc_to_dict(mean_reduced_ndvi).getInfo()

In [55]:
JSON(res)

<IPython.core.display.JSON object>

In [59]:
df = pd.DataFrame(res)

In [70]:
df

NDVI_median  doy system:index
0       0.002589    0   2013_01_01
1       0.007241    1   2013_01_02
2       0.004311    2   2013_01_03
3       0.010822    3   2013_01_04
4       0.006187    4   2013_01_05
..           ...  ...          ...
360     0.014065  360   2013_12_27
361     0.007057  361   2013_12_28
362     0.006408  362   2013_12_29
363     0.005206  363   2013_12_30
364     0.002602  364   2013_12_31

[365 rows x 3 columns]

In [115]:
# Define the degree of the polynomial fits
degree_list = [ 10]

base = alt.Chart(df).mark_circle(color="black",size = 14).encode(
        alt.X("doy:Q"), alt.Y("NDVI_median"),
    tooltip=[
        alt.Tooltip('doy:O', title='DOY'),
        alt.Tooltip('NDVI_median:Q', title='NDVI_median')
    ]
)

polynomial_fit = [
    base.transform_regression(
        "doy", "NDVI_median", method="poly", order=order, as_=["doy", str(order)]
    )
    .mark_line()
    .transform_fold([str(order)], as_=["degree", "NDVI_median"])
    .encode(alt.Color("degree:N"))
    for order in degree_list
]

alt.layer(base, *polynomial_fit).properties(width=1000, height=400)

alt.LayerChart(...)